## Optimal VGG16 Filter Patterns

<img src="http://science.slc.edu/jmarshall/bioai/images/vgg16_architecture.jpg" width="75%">

The VGG16 network, developed by the Visual Geometry Group at Oxford, was trained on the large-scale ImageNet dataset, consisting of 1.4 million labeled images from 1,000 different categories.  Most of these images are of animals or other everyday objects, including many different breeds of cats and dogs.

[K. Simonyan and A. Zisserman, Very deep convolutional networks for large-scale image recognition (2014)](https://arxiv.org/abs/1409.1556) 

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
plt.rcParams["figure.figsize"] = (2,2)  # set default figure size

In [ ]:
import tensorflow
tensorflow.compat.v1.disable_eager_execution()  # workaround for TF2

In [ ]:
from tensorflow.keras.applications import VGG16

vgg16 = VGG16(weights='imagenet', include_top=False)

In [ ]:
vgg16.summary()

### Load the Dataset

In [ ]:
!curl -O science.slc.edu/jmarshall/bioai/data/cats_and_dogs_200.npz

In [ ]:
f = np.load('cats_and_dogs_200.npz')

In [ ]:
images, labels = f['images'], f['labels']

In [ ]:
images.shape

In [ ]:
labels

In [ ]:
plt.imshow(images[0]);

In [ ]:
# general-purpose utility to display VGG16 feature maps for an input image
# example: show_features(vgg16, image, 'block1_conv1')

from tensorflow.keras.applications.imagenet_utils import preprocess_input
from tensorflow.keras.models import Model

def show_vgg16_features(vgg16, image, layer_name, features=range(20), cmap='gray', cols=5):
    # features can be a number like 0 or a sequence like [0, 2, 4] or range(10)
    layer_names = [layer.name for layer in vgg16.layers]
    if layer_name not in layer_names:
        print(f"No such layer: {layer_name}")
        return
    # generate features for layer_name
    input_tensor = vgg16.layers[0].input
    output_tensor = vgg16.get_layer(layer_name).output
    activation_model = Model(inputs=input_tensor, outputs=output_tensor)
    batch = np.array([preprocess_input(image)])
    output = activation_model.predict(batch)[0]
    h, w, d = output.shape
    # display image
    plt.axis('off')
    plt.imshow(image)
    # display feature maps
    if type(features) is int:
        features  = [features]
    rows = len(features) // cols
    if len(features) > rows*cols:
        rows += 1
    fig = plt.figure(figsize=(13, 13/cols*rows))
    i = 1
    for feature in features:
        if 0 <= feature < d:
            fig.add_subplot(rows, cols, i)
            i += 1
            plt.imshow(output[:,:,feature], cmap=cmap)
            plt.title(f"feature {feature}")
            plt.axis('off')

In [ ]:
show_vgg16_features(vgg16, images[0], 'block1_conv1')

In [ ]:
show_vgg16_features(vgg16, images[0], 'block5_conv1')

### Gradients in Keras

In [ ]:
import tensorflow.keras.backend as K

A *placeholder* is a variable that stores a Keras tensor:

In [ ]:
x = K.placeholder(dtype='float32')

In [ ]:
x

As a simple example, we will create a tensor function called `powers` that takes the tensor variable $x$ as input and returns three tensor values representing $x^2$, $x^3$, and $x^4$.  Tensor functions always take a *list* of input variables and return a *list* of output variables.

In [ ]:
powers = K.function([x], [x**2, x**3, x**4])

In [ ]:
powers

In [ ]:
powers([2])

Let's consider the function $y = x^3$

In [ ]:
x

In [ ]:
y = x**3

In [ ]:
y

We can compute the **gradient** $\dfrac{\partial y}{\partial x}$ of the variable $y$ with respect to the variable $x$ using the function `K.gradients`.  You can think of the gradient as representing the amount of *influence* that $x$ exerts on $y$.

In [ ]:
K.gradients(y, x)

In general, this function returns a *list* of gradients, but in this case there is only one.  We need to retrieve it from the list:

In [ ]:
grad = K.gradients(y, x)[0]

In [ ]:
grad

Next, we will create a new function that takes $x$ as input and returns the value of $y$ (that is, $x^3$) together with the value of the gradient $\dfrac{\partial y}{\partial x}$ at $x$:

In [ ]:
compute_value_and_gradient = K.function([x], [y, grad])

In [ ]:
compute_value_and_gradient

With $x = 2$, the value of $y = x^3 = 8$, and the value of $\dfrac{\partial y}{\partial x} = 3x^2 = 12$.

In [ ]:
compute_value_and_gradient([2])

In [ ]:
compute_value_and_gradient([3])

In [ ]:
compute_value_and_gradient([-1])

### Gradient Ascent in One Dimension

Suppose we have a **one-dimensional** space of points $x$ and a function $y$ that specifies the "height" of each point in the space:

$y = 1 - x^2$

In [ ]:
x = np.arange(-1, 1, 0.01)
y = 1 - x**2
plt.figure(figsize=(4,2))
plt.xlabel('x')
plt.title('$y = 1 - x^2$')
plt.plot(x, y);

We can use **gradient ascent** to find the "maximum" point of the space, that is, the point that gives the largest value of $y$ over the entire space.

Start with some value of $x$ and repeat for some number of steps:

* if the gradient $\dfrac{\partial y}{\partial x}$ is **positive**, we **add** a small amount to $x$

* if the gradient $\dfrac{\partial y}{\partial x}$ is **negative**, we **subtract** a small amount from $x$

In [ ]:
x = K.placeholder(dtype='float32')

In [ ]:
y = 1 - x**2

In [ ]:
grad = K.gradients(y, x)[0]

In [ ]:
compute_value_and_gradient = K.function([x], [y, grad])

$y = 1 - x^2$

$\dfrac{\partial y}{\partial x} = -2x$

In [ ]:
compute_value_and_gradient([-1])

We will start at the value $x = -1.0$ and perform 50 "small" steps of gradient ascent.  On each step, we update $x$ by multiplying the step size by the gradient and adding this amount to $x$.  Notice that this is the opposite of what happens in backpropagation, which performs gradient **descent** by negating the step size (*a.k.a.* "learning rate").

In [ ]:
x = -1.0  # starting point

# perform gradient ascent
step_size = 0.1
for i in range(50):
    y, gradient = compute_value_and_gradient([x])
    print(f"x = {x:<12.6f} y = {y:<12.6f} dy/dx = {gradient:<12.6f}")
    x += step_size * gradient  # the backprop rule is -learning_rate * gradient

In [ ]:
# Once again, but this time starting from x = 1

x = 1.0  # starting point

# perform gradient ascent
step_size = 0.1
for i in range(50):
    y, gradient = compute_value_and_gradient([x])
    print(f"x = {x:<12.6f} y = {y:<12.6f} dy/dx = {gradient:<12.6f}")
    x += step_size * gradient

### Gradient Ascent in Two Dimensions

Suppose we have a **two-dimensional** space of points $P = (x_0, x_1)$ and a function $z$ that specifies the "height" of each point in the space:

$z = 1 - (x_0-5)^2 - (x_1-5)^2$

We can use gradient ascent to find the "maximum" point of this space, that is, the point that gives the largest value of $z$ over the entire space.

In [ ]:
import PyGnuplot
fig = PyGnuplot.gp()
fig.c("splot [0:10][0:10] 1 - (x-5)**2 - (y-5)**2")

In [ ]:
P = K.placeholder(shape=(2,), dtype='float32')

In [ ]:
P

In [ ]:
z = 1 - (P[0]-5)**2 - (P[1]-5)**2

In [ ]:
z

We can compute the gradients $\dfrac{\partial z}{\partial x_0}$ and $\dfrac{\partial z}{\partial x_1}$ in one step:

In [ ]:
K.gradients(z, P)

In [ ]:
grad = K.gradients(z, P)[0]  # remove gradient tensor from the list

In [ ]:
grad

Now we will create the all-in-one function `compute_value_and_gradient` that takes a 2-dimensional point $P$ as input, and returns the "height" of the function $z$ at that point, as well as the function's 2-dimensional gradient at $P$.

In [ ]:
compute_value_and_gradient = K.function([P], [z, grad])

In [ ]:
compute_value_and_gradient

$z = 1 - (x_0 - 5)^2 - (x_1 - 5)^2$

$\dfrac{\partial z}{\partial x_0} = -2(x_0 - 5)$

$\dfrac{\partial z}{\partial x_1} = -2(x_1 - 5)$

In [ ]:
point = np.array([7.0, 2.0])

In [ ]:
point

In [ ]:
compute_value_and_gradient([point])

$z = 1 - (7 - 5)^2 - (2 - 5)^2 = 1 - 4 - 9 = -12$

$\dfrac{\partial z}{\partial x_0} = -2(7 - 5) = -4$

$\dfrac{\partial z}{\partial x_1} = -2(2 - 5) = 6$

In [ ]:
current_z, current_grad = compute_value_and_gradient([point])

In [ ]:
current_z, current_grad

In [ ]:
step_size = 0.1

In [ ]:
point

In [ ]:
point += step_size * current_grad

In [ ]:
point

In [ ]:
def print_formatted(z, P, g):
    print("P = [{:>-8.6f} {:>-9.6f}]    z = {:9.5f}     dz/dP = [{:>-9.6f} {:>-9.6f}]"
          .format(P[0], P[1], z, g[0], g[1]))

# starting point
point = np.array([7.0, 2.0])

# perform gradient ascent
step_size = 0.1
for i in range(75):
    current_z, current_grad = compute_value_and_gradient([point])
    print_formatted(current_z, point, current_grad)
    point += step_size * current_grad

### Gradient Ascent in Input Image Space

In [ ]:
150*150*3

We can generate a 3 &times; 3 array of random floating-point numbers in the range 128 to 128+75 (= 203) like this:

In [ ]:
np.random.uniform(128, 128+75, (3,3))

Let's use this approach to generate a blank RGB image containing some random noise:

In [ ]:
blank_image = np.random.uniform(128, 128+75, (150,150,3))

In [ ]:
blank_image.dtype, blank_image.min(), blank_image.max()

In [ ]:
blank_image = blank_image.clip(0, 255).astype('uint8')  # clip isn't necessary here

In [ ]:
blank_image.dtype, blank_image.min(), blank_image.max()

In [ ]:
plt.imshow(blank_image);

The VGG16 input tensor has shape (None,None,None,3), meaning it will be a *batch* of RGB images:

In [ ]:
vgg16.input

The output tensor for layer `block1_conv1` includes all 64 feature maps:

In [ ]:
vgg16.get_layer('block1_conv1').output

Here is the tensor for feature map 0:

In [ ]:
vgg16.get_layer('block1_conv1').output[:,:,:,0]

We can compute the average activation of all units in feature map 0 using the `K.mean` function:

In [ ]:
K.mean(vgg16.get_layer('block1_conv1').output[:,:,:,0])

We will perform gradient ascent to maximize this value with respect to the input tensor `vgg16.input`

In [ ]:
# generates the input pattern that maximally activates the specified filter of a VGG16 layer

def generate_filter_pattern(vgg16, layer_name, filter_index, resolution=150,
                            cycles=300, step_size=1, show=True):
    
    # average activation of the selected feature map is the quantity to maximize

    # create gradient function
    
    # normalize the gradient
    
    # create compute_mean_and_gradient function
    
    # start with a noisy blank image
    
    # perform gradient ascent
    
    # convert input_image array back into a displayable image
    
    
    if show:
        plt.figure(1)
        plt.figure(figsize=(2.5,2.5))
        plt.axis('off')
        num_filters = vgg16.get_layer(layer_name).output_shape[-1]
        plt.title(f"{layer_name} pattern #{filter_index} of {num_filters}")
        plt.imshow(optimal_pattern)
    else:
        return optimal_pattern

In [ ]:
# converts a floating-point array into a displayable RGB image of integers in the range [0, 255]

def deprocess_image(image):
    pass

In [ ]:
generate_filter_pattern(vgg16, 'block1_conv1', 0)

In [ ]:
generate_filter_pattern(vgg16, 'block1_conv1', 7)

In [ ]:
generate_filter_pattern(vgg16, 'block1_conv1', 11)

In [ ]:
generate_filter_pattern(vgg16, 'block1_conv1', 28)

In [ ]:
generate_filter_pattern(vgg16, 'block3_conv1', 0)

Let's define a function to display the optimal patterns for multiple filters in a layer:

In [ ]:
# displays the patterns that maximally activate the specified filters of a VGG16 layer

def show_filter_patterns(vgg16, layer_name, start=0, layout=(10,10), resolution=64,
                         margin=3, transpose=False):
    '''
    each pattern is displayed as a square of resolution x resolution pixels
    in the grid, with margin pixels separating each square.
    '''
    num_filters = vgg16.get_layer(layer_name).output_shape[-1]
    if start >= num_filters:
        print(f"Error: layer '{layer_name}' has only {num_filters} filters")
        return
    rows, cols = layout
    if num_filters < rows*cols:
        rows = num_filters // cols + 1
    # grid must be of type uint8 for plt.imshow to display colors accurately
    grid = np.zeros((rows*resolution + (rows-1)*margin, cols*resolution + (cols-1)*margin, 3),
                    dtype='uint8')
    filter_index = start
    if transpose:
        generator = ((r, c) for c in range(cols) for r in range(rows))
    else:
        generator = ((r, c) for r in range(rows) for c in range(cols))
    for r, c in generator:
        pattern = generate_filter_pattern(vgg16, layer_name, filter_index, resolution,
                                          show=False)
        vert_start = r * (resolution + margin)
        vert_end = vert_start + resolution
        horiz_start = c * (resolution + margin)
        horiz_end = horiz_start + resolution
        grid[vert_start:vert_end, horiz_start:horiz_end, :] = pattern
        filter_index += 1
        if filter_index >= num_filters:
            break
    plt.figure(figsize=(15,15/cols*rows))
    plt.tight_layout()
    plt.axis('off')
    if rows == cols == 1:
        plt.title(f"{layer_name} pattern #{start} of {num_filters}")
    else:
        plt.title(f"{layer_name} patterns #{start}-{filter_index-1} of {num_filters}")
    plt.imshow(grid)

In [ ]:
show_filter_patterns(vgg16, 'block1_conv1')

In [ ]:
show_filter_patterns(vgg16, 'block1_conv1', start=0, layout=(2,6))

In [ ]:
show_filter_patterns(vgg16, 'block2_conv1', start=0, layout=(1,6))

In [ ]:
show_filter_patterns(vgg16, 'block3_conv1', start=0, layout=(1,6))

In [ ]:
show_filter_patterns(vgg16, 'block4_conv1', start=0, layout=(1,6))

In [ ]:
show_filter_patterns(vgg16, 'block5_conv1', start=0, layout=(1,6))

In [ ]:
show_filter_patterns(vgg16, 'block3_conv1', start=100, layout=(8,8)) # need a GPU for this!

In [ ]:
show_filter_patterns(vgg16, 'block4_conv1', start=100, layout=(8,8)) # need a GPU for this!

In [ ]:
show_filter_patterns(vgg16, 'block4_conv1', start=200, layout=(8,8)) # need a GPU for this!

In [ ]:
show_filter_patterns(vgg16, 'block5_conv1', start=100, layout=(8,8)) # need a GPU for this!